## Needed Installs in Jupyter Notebook

In [1]:
!pip install --upgrade Pillow
!pip install tesseract-ocr
!pip install numpy
!pip install tqdm
!pip install os
!pip install codecs
!pip install pytesseract
!pip install opencv-python
!pip install pandas 

  Using cached https://files.pythonhosted.org/packages/2b/65/e4a5130b4162d20ed99ff096549a04d18f050cfcdb16fe1643ac751c0181/Pillow-8.0.1-cp37-cp37m-win_amd64.whl
  Found existing installation: Pillow 6.1.0
    Uninstalling Pillow-6.1.0:
      Successfully uninstalled Pillow-6.1.0
  Running setup.py clean for tesseract-ocr
Failed to build tesseract-ocr
  Running setup.py install for tesseract-ocr: started
    Running setup.py install for tesseract-ocr: finished with status 'error'


  ERROR: Complete output from command 'C:\Users\Light\Anaconda3\python.exe' -u -c 'import setuptools, tokenize;__file__='"'"'C:\\Users\\Light\\AppData\\Local\\Temp\\pip-install-5wys_514\\tesseract-ocr\\setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' bdist_wheel -d 'C:\Users\Light\AppData\Local\Temp\pip-wheel-c0otye54' --python-tag cp37:
  ERROR: running bdist_wheel
  running build
  running build_py
  file tesseract_ocr.py (for module tesseract_ocr) not found
  file tesseract_ocr.py (for module tesseract_ocr) not found
  running build_ext
  building 'tesseract_ocr' extension
  error: Microsoft Visual C++ 14.0 is required. Get it with "Microsoft Visual C++ Build Tools": https://visualstudio.microsoft.com/downloads/
  ----------------------------------------
  ERROR: Failed building wheel for tesseract-ocr
    ERROR: Complete output from command 'C:\Users\Light\A

  ERROR: Could not find a version that satisfies the requirement os (from versions: none)
ERROR: No matching distribution found for os


  ERROR: Could not find a version that satisfies the requirement codecs (from versions: none)
ERROR: No matching distribution found for codecs


  Stored in directory: C:\Users\Light\AppData\Local\pip\Cache\wheels\ee\71\72\b98430261d849ae631e283dfc7ccb456a3fb2ed2205714b63f
Successfully built pytesseract


## Needed Imports

In [4]:

from PIL import Image, ImageDraw, ImageFont
import cv2, pytesseract
import os
import codecs
from tqdm import tqdm
import numpy as np
import sys
import json
from decimal import *
import pandas as pd

## Assigned Path Directories

In [5]:
#path to the the downloaded tesseract exe file in directory 
#paths differ from each Operating system (below it's in Linux environment)
pytesseract.pytesseract.tesseract_cmd = r'C:\Users\Light\Desktop\ocr\tesseract-1.03'    

#set the folders and files paths to avoid heavy calls in the functions 
         #folder created to contained all the results

## From Text file to Images

### Calling the function

In [16]:
#set the folders and files paths to avoid heavy calls in the functions 
corpus_file_name = "C:\\Users\\Light\\Desktop\\ocr\\medicalwords_ismael.txt"                
errors_path = 'C:\\Users\\Light\\Desktop\\ocr\\errors\\'
image_files_path = "C:\\Users\\Light\\Desktop\\ocr\\images\\"         
ocr = "C:\\Users\\Light\\Desktop\\ocr\\" 

def create_images(corpus_file_name, image_files_path, font = 'arialuni'):
    '''for every single line in the medical word txt file, this function will create and assign and image'''
    
    #try:
    f = open(corpus_file_name, "r", encoding='utf-8')   #encoding type is important     
    fl = f.readlines()
    fl = tqdm(fl)      #tqdm allows to estimate to progess in runtime. It can be important

    #download arialuni.ttf from browser and drag the location here into ImageFont.truetype 
    fnt = ImageFont.truetype(r'C:\\Users\\Light\\Desktop\\ocr\\arialuni.ttf', 20) 
    #autamatically create an "error" txt file in case 
    errorfile = codecs.open(errors_path + 'errors_in_create_images.txt', 'w', encoding = 'utf-8')

    for l in fl:
        #try:
        # image width is 150 if number of characters is upto 10 else it is 300
        # imagebackground is white, text is black
        if (len(l) <= 10):
            img = Image.new('RGB', (150, 40), color = (255,255,255))
        else:
            img = Image.new('RGB', (300, 40), color = (255,255,255)) 
        d = ImageDraw.Draw(img)

        #strip newline
        word = l.rstrip()                
        d.multiline_text((10,10), word, fill="black",spacing = 0, align  = "right", font = fnt)

        img.save(f'{image_files_path}{word}.png')  #each image will be saved under the associated word 

            #except Exception as runtime_except:             #in case of errors in the loop try
                #print('\n Handling error in loop try: create_images:')
                #errorfile.write('\n Handling error in loop try: create_images:' + ' ')
                #pass      
            
    #except Exception as runtime_except:                     #in case of errors in the main try 
     #   print('\n Handling error in main try : create_images:')
     #   errorfile.write('\n Handling error in main try : create_images:')
    #errorfile.close

### Running the function 

In [17]:
def main():
    create_images(corpus_file_name, image_files_path, font = 'arialuni')
    
if __name__ == "__main__":
    main()

100%|█████████████████████████████████████████████████████████████████████████████| 1746/1746 [00:14<00:00, 123.09it/s]


## Frome Images to Tesseract Annotations

### Calling the function 

In [18]:
#set the folders and files paths to avoid heavy calls in the functions
annotatins_path = "C:\\Users\\Light\\Desktop\\ocr\\annotations"            #folder that will contain annotations in ocr


def generate_annotation(image_files_path):
    '''For every single image, this function will produce a tesseract annotation that labels each letter in the word (bounding boxes)'''
    
    try:
        # words that have no characters recognized
        error_words = []
        words_written_counter = 0
        
        # output file into which bounding boxes are written
        f = open("C:\\Users\\Light\\Desktop\\ocr\\annotations\\annotations.txt","w+")  #write the annotations txt file
        for filename in tqdm(os.listdir(image_files_path)): #tqdm allows to estimate to progess in runtime. It can be important
            try:
                img = cv2.imread(f'{image_files_path}/{filename}') #read the image at this exact location
                h, w, _ = img.shape #assumes color image

                # run tesseract, returning the bounding boxes
                boxes = pytesseract.image_to_boxes(img, lang='eng') #include and adapt any configuration options you use

                if (len(boxes.splitlines()) == 0):
                    error_words.append(filename.split('.')[0])
                else:
                    # draw the bounding boxes on the image
                    f.write('\n')
                    for b in boxes.splitlines():
                        f.write(filename + ' ' + str(b) + '\n')  #label
                        words_written_counter = words_written_counter + 1
                    if (words_written_counter % 500 == 0):       #to keep track on the tqdm progress in the labelling
                        print(words_written_counter , 'Files Processed Successfully')
                        
            except Exception as runtime_except:                  #in case of errors in the loop try
                print(f' handling error in loop try: exception in generate_annotation {filename}', runtime_except)
                pass            
        f.close()
        
    except Exception as runtime_except:                          #in case of errors in the main try
            print('Handling error in main try : generate_annotation:', runtime_except)
    return(error_words, len(error_words))

### Running the function 

In [19]:
def main():
    generate_annotation(image_files_path)
    
if __name__ == "__main__":
    main()

  0%|                                                                                         | 0/1731 [00:00<?, ?it/s]

 handling error in loop try: exception in generate_annotation ABSORBABLE.png [WinError 5] Access is denied


  0%|                                                                                 | 1/1731 [00:01<39:50,  1.38s/it]

 handling error in loop try: exception in generate_annotation acrocephalosyndactyly.png [WinError 5] Access is denied
 handling error in loop try: exception in generate_annotation activating factor.png [WinError 5] Access is denied
 handling error in loop try: exception in generate_annotation acute glaucoma.png [WinError 5] Access is denied


  0%|▏                                                                                | 4/1731 [00:01<28:12,  1.02it/s]

...

100%|█████████████████████████████████████████████████████████████████████████████▋| 1725/1731 [00:48<00:00, 42.83it/s]

 handling error in loop try: exception in generate_annotation volume reduction.png [WinError 5] Access is denied
 handling error in loop try: exception in generate_annotation WALL DEFECTS.png [WinError 5] Access is denied
 handling error in loop try: exception in generate_annotation white cell.png [WinError 5] Access is denied
 handling error in loop try: exception in generate_annotation Willebrand disease.png [WinError 5] Access is denied
 handling error in loop try: exception in generate_annotation X-ray.png [WinError 5] Access is denied


100%|█████████████████████████████████████████████████████████████████████████████▉| 1730/1731 [00:48<00:00, 43.48it/s]

 handling error in loop try: exception in generate_annotation young diabetes.png [WinError 5] Access is denied


100%|██████████████████████████████████████████████████████████████████████████████| 1731/1731 [00:48<00:00, 35.78it/s]


## From tesseract annotations to vgg annotations

### Calling the function 

In [1]:
#set the folders and files paths to avoid heavy calls in the functions
vgg = "C:\Users\Light\Desktop\ocr\vgg\vgg.txt"                         #file containing vgg annotations 
annotations = "C:\Users\Light\Desktop\ocr\annotations.txt" #file containing images annotations 


def convert_tesseract_to_vgg(annotations, vgg, encoding = 'latin1'):
    ''' This will help in converting from tesseract annotation to vgg annotation. 
        The target format is: Anesthetist.png,1076,"{}",11,1,"{""name"":""rect"",""x"":10,""y"":8,""width"":17,""height"":22}","{""name"":""A""}" 
        The source format is: Anesthetist.png A 10 8 17 22 0'''
    
    # holds all the lines for a word, one line for each character
    lines = ""
    title = ""
    
    #number of letters in the word
    letter_counter = 1
    
    #number of exceptions
    error_counter = 0
    outputfile = codecs.open(vgg, 'w', encoding = 'utf-8') #write file that will contain the vgg annotations 
    errorfile = codecs.open('errors_in_to_vgg.txt', 'w', encoding = 'utf-8') #file that will contain errors in case
    
    # header for the file
    title_words = ['filename',
                   'file_size',
                   'file_attributes',
                   'region_count',
                   'region_id',
                   'region_shape_attributes',
                   'region_attributes']
    
    for word in title_words:
        title = title + word + ','
    title = title + '\n'    
    outputfile.write(title)
    
    for each_line in open(annotations, "r", encoding =  'utf-8'):
        try:        
            if (each_line == "\n"):      #If empty line, then new word begining and write the previous word to file
                if len(lines) > 0:
                    lines = lines.replace("$", str(letter_counter-1)) # $ is the place holder for number of letters
                    letter_counter = 1               # reset letter counter
                    outputfile.write(lines)          # write all the lines (one for each letter) 
                    outputfile.write("\n")           # write new line
                    lines = ""                       # reset the lines for next word to empty
            else:
                # single word file name
                if len(each_line.split(' '))  == 7:
                    filename, letter, x, y, width, height, _ = each_line.split(' ') # not working for multiline words
                    
                #double word filen name
                elif len(each_line.split(' ')) == 8:
                    filenamew1, filenamew2, letter, x, y, width, height, _ = each_line.split(' ')
                    filename = filenamew1 + ' ' + filenamew2
                    
                #three words file name
                elif len(each_line.split(' ')) == 9:
                    filenamew1, filenamew2, filenamew3, letter, x, y, width, height, _ = each_line.split(' ')
                    filename = filenamew1 + ' ' + filenamew2 + ' ' + filenamew3
                 
                # file size is set to dummy value of 1076
                lines = lines + filename + "," + "1076,\"{}\"," + "$," + str(letter_counter) + "," + "\"{\"\"name\"\":" + "\"\"rect\"\","+ "\"\"x\"\"" + ":" + str(x) + ",\"\"y\"\"" + ":" + str(y) + ",\"\"width\"\"" + ":" + str(width) + ",\"\"height\"\"" + ":" + str(height) + "}\",\"{\"\"name\"\":" + "\"\"" + str(letter) + "\"\"}\"" +"\n"
                letter_counter = letter_counter + 1
                
        except Exception as runtime_except:        #in case of errors 
            print(each_line)
            errorfile.write(each_line)            
            print('error in converting to vgg for line:', each_line)
            error_counter = error_counter + 1
            print(runtime_except)
            pass
        
    errorfile.close()
    return(error_counter)

### Running the function 

In [4]:
def main():
    convert_tesseract_to_vgg(annotations, vgg, encoding = 'latin1')
    
if __name__ == "__main__":
    main()

### Coping the resulted txt file into a csv file 

In [5]:
#converting the vgg.txt file in to .csv

read_file = pd.read_csv (r"C:\Users\Light\Desktop\ocr\vgg\vgg.txt")
read_file.to_csv (r'C:\Users\Light\Desktop\ocr\vgg\vgg.csv', index=None)

## From vgg to yolo annotation format

### Calling the function 

In [6]:
#set the folders and files paths to avoid heavy calls in the functions
vgg_csv = "vgg.csv"
vgg_csv_path = "C:\Users\Light\Desktop\ocr\vgg\"



#this is our dictionnary: to each alphabetic character including "-"" and "_" we assign a number 
letter_to_class_map = thisdict = {
  "a": "0",
  "b": "1",
  "c": "2",
  "d": "3",
  "e": "4",
  "f": "4",
  "g": "6",
  "h": "7",
  "i": "8",
  "j": "9",
  "k": "10",
  "l": "11",
  "m": "12",
  "n": "13",
  "o": "14",
  "p": "15",
  "q": "16",
  "r": "17",
  "s": "18",
  "t": "19",
  "u": "20",
  "v": "21",
  "w": "22",
  "x": "23",
  "y": "24",
  "z": "25",
  "-": "26",
  "A": "27",
  "B": "28",
  "C": "29",
  "D": "30",
  "E": "31",
  "F": "32",
  "G": "33",
  "H": "34",
  "I": "35",
  "J": "36",
  "K": "37",
  "L": "38",
  "M": "39",
  "N": "40",
  "O": "41",
  "P": "42",
  "Q": "43",
  "R": "44",
  "S": "45",
  "T": "46",
  "U": "47",
  "V": "48",
  "W": "49",
  "X": "50",
  "Y": "51",
  "Z": "52",
  "_": "53"    
}


def convert_vgg_yolo(vgg_csv, image_files_path,):
    """"This function allows to convert the vgg annotations in the csv file into a txt file following the yolo annotations"""
    
    f = open(vgg_csv_path + vgg_csv, "r", encoding='utf-8') #read the vgg annotations csv file
    
    i = 0
    newfile = True
    for line in f:
        try:
            i = i + 1
            
            #skip header
            if ( i == 1):
                continue;  

            #for new line, close current file and create new file
            #one annotation file will be created for one image file
            #in the same folder as images
            if(line == "\n"):
                output_file_.close()
                newfile = True
                continue;
            elif(newfile == True):
                filename = line.split(',')[0]
                output_file_ = codecs.open(image_files_path + filename.split(".")[0] + '.txt', 'a', encoding = 'utf-8')   #append the lines of labelling of every single letter of the word assign to the image
                newfile = True
                        
            #filename = line.split(',')[0]
            x = line.split(',')[6].split(":")[1]
            y = line.split(',')[7].split(":")[1]
            width = line.split(',')[8].split(":")[1]
            height = line.split(',')[9].split(":")[1].split('}')[0]
            obj_class = line.split(',')[10].split(":")[1][2]
            obj_class = letter_to_class_map.get(obj_class)
            x = float(x)
            y = float(y)
            width = float(width)
            height = float(height)
            print(line)
            
            img = Image.open(image_files_path + filename)
            size = img.size
            print(x, y, width, height, size[0], size[1])
            
            #Re-Dimensioning in order to fit the yolo format
            _x      = Decimal(x + width) / Decimal(2 * size[0]) # relative position of center x of rect
            _y      = Decimal(y + height) / Decimal(2 * size[1]) # relative position of center y of rect
            _width  = Decimal(width / size[0])
            _height = Decimal(height / size[1])
            
            #write in created output_file_ txt file (obj_class, round(_x, 10), round(_y, 10), round(_width, 10), round(_height, 10))
            #this is the yolo annotation format we are aiming
            output_file_.write(str(obj_class) + " " + str(round(_x, 10)) + " " + str(round(_y, 10)) + " " + str(round(_width, 10)) + " " + str(round(_height, 10)))
            output_file_.write("\n")
            print(_x, _y, _width, _height)
            
        except Exception as runtime_except:       #in case of errors 
            print('exception')
            print(runtime_except)
            print(line)
            print("{0:.10f} {0:.10f} {0:.10f} {0:.10f}".format(_x, _y, _width, _height))
            pass
    output_file_.close()

### Running the function 

In [9]:
def main():
    convert_vgg_yolo(vgg_csv, image_files_path, yolo)
    
if __name__ == "__main__":
    main()

Anesthetist.png,1076,{},11,1,"{""name"":""rect"",""x"":10,""y"":8,""width"":17,""height"":22}","{""name"":""A""}",

10.0 8.0 17.0 22.0 300 40
0.045 0.375 0.056666666666666663798590519718345603905618190765380859375 0.5500000000000000444089209850062616169452667236328125
Anesthetist.png,1076,{},11,2,"{""name"":""rect"",""x"":17,""y"":8,""width"":23,""height"":22}","{""name"":""n""}",

17.0 8.0 23.0 22.0 300 40
0.06666666666666666666666666667 0.375 0.076666666666666660745477201999165117740631103515625 0.5500000000000000444089209850062616169452667236328125
Anesthetist.png,1076,{},11,3,"{""name"":""rect"",""x"":25,""y"":8,""width"":33,""height"":18}","{""name"":""e""}",

25.0 8.0 33.0 18.0 300 40
0.09666666666666666666666666667 0.325 0.11000000000000000055511151231257827021181583404541015625 0.450000000000000011102230246251565404236316680908203125
Anesthetist.png,1076,{},11,4,"{""name"":""rect"",""x"":35,""y"":8,""width"":44,""height"":18}","{""name"":""s""}",

35.0 8.0 44.0 18.0 300 40
0.13

0.09833333333333333333333333333 0.325 0.11000000000000000055511151231257827021181583404541015625 0.450000000000000011102230246251565404236316680908203125
Aneurysm aortic.png,1076,{},14,4,"{""name"":""rect"",""x"":37,""y"":8,""width"":44,""height"":18}","{""name"":""u""}",

37.0 8.0 44.0 18.0 300 40
0.135 0.325 0.146666666666666667406815349750104360282421112060546875 0.450000000000000011102230246251565404236316680908203125
Aneurysm aortic.png,1076,{},14,5,"{""name"":""rect"",""x"":49,""y"":8,""width"":55,""height"":18}","{""name"":""r""}",

49.0 8.0 55.0 18.0 300 40
0.1733333333333333333333333333 0.325 0.1833333333333333203807313793731736950576305389404296875 0.450000000000000011102230246251565404236316680908203125
Aneurysm aortic.png,1076,{},14,6,"{""name"":""rect"",""x"":58,""y"":4,""width"":66,""height"":18}","{""name"":""y""}",

58.0 4.0 66.0 18.0 300 40
0.2066666666666666666666666667 0.275 0.2200000000000000011102230246251565404236316680908203125 0.450000000000000011102230246251565

Aneurysm arteriosclerotic.png,1076,{},24,11,"{""name"":""rect"",""x"":118,""y"":8,""width"":125,""height"":21}","{""name"":""t""}",

118.0 8.0 125.0 21.0 300 40
0.405 0.3625 0.416666666666666685170383743752609007060527801513671875 0.52500000000000002220446049250313080847263336181640625
Aneurysm arteriosclerotic.png,1076,{},24,12,"{""name"":""rect"",""x"":125,""y"":8,""width"":129,""height"":21}","{""name"":""e""}",

125.0 8.0 129.0 21.0 300 40
0.4233333333333333333333333333 0.3625 0.429999999999999993338661852249060757458209991455078125 0.52500000000000002220446049250313080847263336181640625
Aneurysm arteriosclerotic.png,1076,{},24,13,"{""name"":""rect"",""x"":134,""y"":8,""width"":140,""height"":18}","{""name"":""r""}",

134.0 8.0 140.0 18.0 300 40
0.4566666666666666666666666667 0.325 0.46666666666666667406815349750104360282421112060546875 0.450000000000000011102230246251565404236316680908203125
Aneurysm arteriosclerotic.png,1076,{},24,14,"{""name"":""rect"",""x"":142,""y"":8,""width"

216.0 8.0 225.0 22.0 300 40
0.735 0.375 0.75 0.5500000000000000444089209850062616169452667236328125
Aneurysm atherosclerotic.png,1076,{},23,23,"{""name"":""rect"",""x"":227,""y"":8,""width"":236,""height"":18}","{""name"":""c""}",

227.0 8.0 236.0 18.0 300 40
0.7716666666666666666666666667 0.325 0.786666666666666625218340413994155824184417724609375 0.450000000000000011102230246251565404236316680908203125
Aneurysm berry.png,1076,{},13,1,"{""name"":""rect"",""x"":10,""y"":8,""width"":16,""height"":22}","{""name"":""A""}",

10.0 8.0 16.0 22.0 300 40
0.04333333333333333333333333333 0.375 0.053333333333333336756520992594232666306197643280029296875 0.5500000000000000444089209850062616169452667236328125
Aneurysm berry.png,1076,{},13,2,"{""name"":""rect"",""x"":16,""y"":8,""width"":23,""height"":22}","{""name"":""n""}",

16.0 8.0 23.0 22.0 300 40
0.065 0.375 0.076666666666666660745477201999165117740631103515625 0.5500000000000000444089209850062616169452667236328125
Aneurysm berry.png,1076,{},1

Aneurysm cardiac.png,1076,{},15,8,"{""name"":""rect"",""x"":77,""y"":8,""width"":94,""height"":18}","{""name"":""m""}",

77.0 8.0 94.0 18.0 300 40
0.285 0.325 0.31333333333333335257719909350271336734294891357421875 0.450000000000000011102230246251565404236316680908203125
Aneurysm cardiac.png,1076,{},15,9,"{""name"":""rect"",""x"":107,""y"":8,""width"":108,""height"":18}","{""name"":""c""}",

107.0 8.0 108.0 18.0 300 40
0.3583333333333333333333333333 0.325 0.35999999999999998667732370449812151491641998291015625 0.450000000000000011102230246251565404236316680908203125
Aneurysm cardiac.png,1076,{},15,10,"{""name"":""rect"",""x"":108,""y"":8,""width"":116,""height"":18}","{""name"":""a""}",

108.0 8.0 116.0 18.0 300 40
0.3733333333333333333333333333 0.325 0.386666666666666658525031152748852036893367767333984375 0.450000000000000011102230246251565404236316680908203125
Aneurysm cardiac.png,1076,{},15,11,"{""name"":""rect"",""x"":121,""y"":8,""width"":126,""height"":18}","{""name"":""r""}",



...

12.0 8.0 19.0 22.0 300 40
0.05166666666666666666666666667 0.375 0.06333333333333333869941128568825661204755306243896484375 0.5500000000000000444089209850062616169452667236328125
REGURGITATION VALVE.png,1076,{},18,2,"{""name"":""rect"",""x"":26,""y"":8,""width"":33,""height"":22}","{""name"":""E""}",

26.0 8.0 33.0 22.0 300 40
0.09833333333333333333333333333 0.375 0.11000000000000000055511151231257827021181583404541015625 0.5500000000000000444089209850062616169452667236328125
REGURGITATION VALVE.png,1076,{},18,3,"{""name"":""rect"",""x"":38,""y"":8,""width"":47,""height"":22}","{""name"":""G""}",

38.0 8.0 47.0 22.0 300 40
0.1416666666666666666666666667 0.375 0.156666666666666676288599546751356683671474456787109375 0.5500000000000000444089209850062616169452667236328125
REGURGITATION VALVE.png,1076,{},18,4,"{""name"":""rect"",""x"":47,""y"":8,""width"":51,""height"":22}","{""name"":""U""}",

47.0 8.0 51.0 22.0 300 40
0.1633333333333333333333333333 0.375 0.17000000000000001221245327087672

CATHETER.png,1076,{},8,7,"{""name"":""rect"",""x"":90,""y"":8,""width"":98,""height"":22}","{""name"":""E""}",

90.0 8.0 98.0 22.0 150 40
0.6266666666666666666666666667 0.375 0.65333333333333332149095440399833023548126220703125 0.5500000000000000444089209850062616169452667236328125
CATHETER.png,1076,{},8,8,"{""name"":""rect"",""x"":103,""y"":8,""width"":115,""height"":22}","{""name"":""R""}",

103.0 8.0 115.0 22.0 150 40
0.7266666666666666666666666667 0.375 0.76666666666666671847707448250730521976947784423828125 0.5500000000000000444089209850062616169452667236328125
CONNECTOR.png,1076,{},9,1,"{""name"":""rect"",""x"":11,""y"":8,""width"":20,""height"":22}","{""name"":""C""}",

11.0 8.0 20.0 22.0 150 40
0.1033333333333333333333333333 0.375 0.1333333333333333314829616256247390992939472198486328125 0.5500000000000000444089209850062616169452667236328125
CONNECTOR.png,1076,{},9,2,"{""name"":""rect"",""x"":25,""y"":8,""width"":35,""height"":22}","{""name"":""O""}",

25.0 8.0 35.0 22.0 150 40

84.0 8.0 91.0 22.0 150 40
0.5833333333333333333333333333 0.375 0.6066666666666666873908297930029220879077911376953125 0.5500000000000000444089209850062616169452667236328125
CANISTER.png,1076,{},8,8,"{""name"":""rect"",""x"":97,""y"":8,""width"":109,""height"":22}","{""name"":""R""}",

97.0 8.0 109.0 22.0 150 40
0.6866666666666666666666666667 0.375 0.72666666666666668294993769450229592621326446533203125 0.5500000000000000444089209850062616169452667236328125
FILTER.png,1076,{},6,1,"{""name"":""rect"",""x"":12,""y"":8,""width"":18,""height"":22}","{""name"":""F""}",

12.0 8.0 18.0 22.0 150 40
0.1 0.375 0.11999999999999999555910790149937383830547332763671875 0.5500000000000000444089209850062616169452667236328125
FILTER.png,1076,{},6,2,"{""name"":""rect"",""x"":24,""y"":8,""width"":26,""height"":22}","{""name"":""I""}",

24.0 8.0 26.0 22.0 150 40
0.1666666666666666666666666667 0.375 0.173333333333333339254522798000834882259368896484375 0.5500000000000000444089209850062616169452667236328125


SINGLE PATIENT.png,1076,{},13,12,"{""name"":""rect"",""x"":148,""y"":8,""width"":157,""height"":22}","{""name"":""N""}",

148.0 8.0 157.0 22.0 300 40
0.5083333333333333333333333333 0.375 0.52333333333333331705006230549770407378673553466796875 0.5500000000000000444089209850062616169452667236328125
SINGLE PATIENT.png,1076,{},13,13,"{""name"":""rect"",""x"":160,""y"":8,""width"":172,""height"":22}","{""name"":""T""}",

160.0 8.0 172.0 22.0 300 40
0.5533333333333333333333333333 0.375 0.57333333333333336145898329050396569073200225830078125 0.5500000000000000444089209850062616169452667236328125
Adenosine.png,1076,{},9,1,"{""name"":""rect"",""x"":10,""y"":8,""width"":16,""height"":22}","{""name"":""A""}",

10.0 8.0 16.0 22.0 150 40
0.08666666666666666666666666667 0.375 0.10666666666666667351304198518846533261239528656005859375 0.5500000000000000444089209850062616169452667236328125
Adenosine.png,1076,{},9,2,"{""name"":""rect"",""x"":16,""y"":8,""width"":23,""height"":22}","{""name"":""d""}",



0.07 0.375 0.0733333333333333337034076748750521801412105560302734375 0.5500000000000000444089209850062616169452667236328125
Emergency Room.png,1076,{},13,3,"{""name"":""rect"",""x"":31,""y"":8,""width"":38,""height"":18}","{""name"":""e""}",

31.0 8.0 38.0 18.0 300 40
0.115 0.325 0.1266666666666666773988225713765132240951061248779296875 0.450000000000000011102230246251565404236316680908203125
Emergency Room.png,1076,{},13,4,"{""name"":""rect"",""x"":41,""y"":8,""width"":50,""height"":18}","{""name"":""r""}",

41.0 8.0 50.0 18.0 300 40
0.1516666666666666666666666667 0.325 0.1666666666666666574148081281236954964697360992431640625 0.450000000000000011102230246251565404236316680908203125
Emergency Room.png,1076,{},13,5,"{""name"":""rect"",""x"":52,""y"":4,""width"":64,""height"":18}","{""name"":""g""}",

52.0 4.0 64.0 18.0 300 40
0.1933333333333333333333333333 0.275 0.2133333333333333470260839703769306652247905731201171875 0.450000000000000011102230246251565404236316680908203125
Emergency 